# MIDI and Audio

This notebook contains the actual music produced, as well as some information about the NES music.

In [2]:
import pickle
from IPython.display import Audio
from nesmdb.convert import seprsco_to_wav,exprsco_to_wav

# 1. Playing results from the models.

## 1. Testing the model with the nesmdb library.

In this section, we examine the interpolations between song bits. For reference, we produce the two songs then present the interpolation.

### 1.1. The first part.

In [96]:
with open('begin.pickle', 'rb') as f:
    exprsco = pickle.load(f)
wav = seprsco_to_wav(exprsco)
Audio(wav, rate=44100)

### 1.2. The last part.

In [95]:
with open('end.pickle', 'rb') as f:
    exprsco = pickle.load(f)
wav = seprsco_to_wav(exprsco)
Audio(wav, rate=44100)

### 1.3. The interpolation.

In [100]:
with open('test_sample.pickle', 'rb') as f:
    exprsco = pickle.load(f)

exprsco[2].shape
wav = seprsco_to_wav(exprsco)
Audio(wav, rate=44100)

### 1.4. Save the song.

In [101]:
from scipy.io.wavfile import write
write('sample_c.wav', 44100,wav)

## 2. MIDI Information

We take a moment to consider MIDI information. All of the MIDI files will have a resolution of 22050 as well as a BPM of 120, therefore reach tick amounts to roughly $9.07 \times 10^{-5}$ seconds. 

We take a moment to consider MIDI information. Each MIDI file consists of 5 tracks. The first track consists of four events for all songs. The only difference accross songs is the number of ticks for the third event, which accounts for the duration of the song. Otherwise, the tick account is 0,0,$x$,1, where $x$ is the tick count for the third event. The remaining four tracks correspond to P1, P2, TR, and NO, in that order. 

In [9]:
import midi
midi_name = 'nesmdb_midi/train/325_SuperMarioWorld_12_13GameClear.mid'
midi_name2 = 'nesmdb_midi/train/221_MarioBros__00_01TitleBGM.mid'
pattern = midi.read_midifile(midi_name2)
print "Number of tracks: {}".format(len(pattern))
print "Example of a track. Track size: " + str(len(pattern[2]))
pattern[1]

Number of tracks: 5
Example of a track. Track size: 370


midi.Track(\
  [midi.TrackNameEvent(tick=0, text='p1', data=[112, 49]),
   midi.ProgramChangeEvent(tick=0, channel=0, data=[80]),
   midi.NoteOnEvent(tick=231, channel=0, data=[69, 15]),
   midi.ControlChangeEvent(tick=1239, channel=0, data=[11, 14]),
   midi.ControlChangeEvent(tick=1423, channel=0, data=[11, 13]),
   midi.ControlChangeEvent(tick=1237, channel=0, data=[11, 12]),
   midi.ControlChangeEvent(tick=1238, channel=0, data=[11, 11]),
   midi.ControlChangeEvent(tick=1239, channel=0, data=[11, 10]),
   midi.ControlChangeEvent(tick=1422, channel=0, data=[11, 9]),
   midi.ControlChangeEvent(tick=1238, channel=0, data=[11, 8]),
   midi.ControlChangeEvent(tick=1238, channel=0, data=[11, 7]),
   midi.ControlChangeEvent(tick=1238, channel=0, data=[11, 6]),
   midi.ControlChangeEvent(tick=1423, channel=0, data=[11, 5]),
   midi.ControlChangeEvent(tick=1238, channel=0, data=[11, 4]),
   midi.ControlChangeEvent(tick=1237, channel=0, data=[11, 3]),
   midi.NoteOnEvent(tick=507, channel=0,

In [15]:
secs_per_tick = (pattern[0][0].get_bpm()/pattern.resolution)/60
ticks_per_sec = 1/secs_per_tick
print "There are " + str(ticks_per_sec) + " ticks in a second."
print "There are " + str(ticks_per_sec/24) + " ticks in a unit of time of scores."

There are 11025.0 ticks in a second.
There are 459.375 ticks in a unit of time of scores.


There are five type of events, each with a "data" feature, consisting of a list of one or two elements as well as a "channel", denoted as an integer. The channel is completely determined by the voice, so we ignore it for the time being.


The events are as follows:

    1. TrackNameEvent
    2. ProgramChangeEvent
    3. ControlChangeEvent
    4. NoteOnEvent
    5. EndOfTrackEvent

The `TrackNameEvent` only occurs at the beginning, and only tells us what voice the track is using, similarly for the `EndofTrackEvent`. We can thus safely ignore these two. The `ProgramChangeEvent` also only occurs once, as the second element of the track. Both the data feature and the channel are completely determined by the voice, so we can also safely ignore it as well.

     Channel:                  Data for ProgramChangeEvent:
     P1: 0                     P1: 80
     P2: 1                     P2: 81
     TR: 2                     TR: 38
     NO: 9                     NO: 121

Thus, the only important events are `NoteOnEvent` and `ControlChangeEvent`. The former marks the beginning of a note, as well as the velocity. The data "feature" contains two entries, consisting of the note value as well as the velocity. For each instrument, we can only have one note at a time, so in order to play a different note, we have to have another `NoteOnEvent` with the same note, but velocity 0 (marking the end of that note), then another `NoteOnEvent` denoting the note when we want to play. Might be reasonable during modeling to merge these two, but for the purposes of making MIDI files, it's important. 

The `ControlChangeEvent` marks when we change velocity or timbre of the note. Each of these events has a "data" feature, which consist of two numbers. The first one is either 11 (corresponding to velocity change) or 12 (corresponding to timbre change), and the second marks the new value. 

Therefore, we can make the following count (ignoring ticks):

    P1/P2:
    NoteOnEvent Count:        1232 (= 77 notes x 16 velocities)
    ControlChangeEvent Count: 20   (= 4 timbres + 16 velocities)

    TR: 
    NoteOnEvent Count:        89
    ControlChangeEvent Count: 0    (= 0 velocities + 0 timbres)

    NO:
    NoteOnEvent Count:        272  (= 17 notes x 16 velocities)
    ControlChangeEvent Count: 18   (= 16 velocities + 2 timbres)

We can also consider thinking about ticks. How long are they? We know 
$$\text{tick_length} = \text{BPms}/\text{Resolution}$$

All the MIDI files have the same resolution: 22050.

## 3. Effects of transformation on music.

In this section, we examine what effects certain transformations have on how the music sound. We will be working primarily with the seperated score, but for completion, we include the expressive score version here.

In [29]:
exprsco_name = 'nesmdb24_exprsco/train/221_MarioBros__00_01TitleBGM.exprsco.pkl'
with open(exprsco_name, 'rb') as f:
    rate, nsamps, exprsco = pickle.load(f)
wav = exprsco_to_wav((rate,nsamps, exprsco))
Audio(wav,rate=44100)

### 3.1. Reference MIDI.

We will be focusing on this particular MIDI file.

In [30]:
#seprsco_name = 'nesmdb24_seprsco/train/221_MarioBros__00_01TitleBGM.seprsco.pkl'
seprsco_name = 'nesmdb24_seprsco/train/221_MarioBros__01_02GameStartA.seprsco.pkl'
with open(seprsco_name, 'rb') as f:
    rate, nsamps, seprsco = pickle.load(f)
wav = seprsco_to_wav((rate,nsamps, seprsco))
Audio(wav,rate=44100)

### 3.2. Removing NO voice.

In [32]:
no_NO_seprsco = seprsco
no_NO_seprsco[:,2] = 0
no_NO_seprsco[:,3] = 0
wav = seprsco_to_wav((rate,nsamps,no_NO_seprsco))
Audio(wav,rate=44100)

### 3.3. Transposing

By transposing, I mean shifting the notes by a constant amount. We explore with a few values. It seems like transposing by up to 4 notes in either direction still retains musical flavor.

In [33]:
import numpy as np
f = np.vectorize(lambda x : x - 1 if 0 < x < 108 else 0)
f_seprsco =  f(no_NO_seprsco)
wav = seprsco_to_wav((rate,nsamps,f_seprsco))
Audio(wav,rate=44100)

### 3.4. Thresholding.

In [22]:
with open(seprsco_name, 'rb') as g:
    test = pickle.load(g)
wav = seprsco_to_wav(test)
Audio(wav, rate=44100)

/home/xavier/.local/lib/python2.7/site-packages/IPython/lib/display.py:135: RuntimeWarning: invalid value encountered in divide
  scaled = np.int16(data/np.max(np.abs(data))*32767).tolist()


## 4. Human-based restriction of the data.

Some songs don't sound quite nicely when chopped up. In attempt to fix this problem, this section contains code for the bored reader to listen to music and find the good songs.

In [75]:
import glob
import pickle
from IPython.display import Audio
from nesmdb.convert import seprsco_to_wav
a = list(glob.glob('nesmdb24_seprsco/train/*'))
#with open(a, 'rb') as f:
#    (a,b,seprsco) = pickle.load(f)

#seprsco[:,2] = 0
#seprsco[:,3] = 0
#wav = seprsco_to_wav((a,b,seprsco))
#Audio(wav, rate=44100)
good_songs = [0,3,4,5,6,7,10,11,16]

In [77]:
a[16]

'nesmdb24_seprsco/train/380_WaronWheels_10_11ResultsTheme.seprsco.pkl'